In [1]:
import sys
import os
sys.path.insert(0, os.getcwd())
from data.utils import data_split
import pickle

with open("/mnt/lustre/chenyun/jpx_trading/PortfolioOpt-main/data/jpx_data/data_scale.pkl", 'rb') as f:
    df = pickle.load(f)
df = df.sort_values(['date', 'tic']).reset_index(drop=True)
print(df)



train = data_split(df, '2017-01-05', '2020-11-22')

test = data_split(df, '2020-11-22', '2021-12-03')
df.index = df['date'].factorize()[0]
whole_data = df

/mnt/cache/chenyun/anaconda3/envs/gnn/lib/python3.9/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


              date   tic      open      high       low     close    volume  \
0       2017-01-04  1407  1.000000  1.000000  1.000000  1.000000  1.000000   
1       2017-01-04  1414  1.000000  1.000000  1.000000  1.000000  1.000000   
2       2017-01-04  1435  1.000000  1.000000  1.000000  1.000000  1.000000   
3       2017-01-04  1515  1.000000  1.000000  1.000000  1.000000  1.000000   
4       2017-01-04  1766  1.000000  1.000000  1.000000  1.000000  1.000000   
...            ...   ...       ...       ...       ...       ...       ...   
600495  2021-12-03  9936  1.015571  1.011824  1.010381  1.022222  0.515030   
600496  2021-12-03  9983  0.998941  0.986455  1.004147  0.992702  0.962545   
600497  2021-12-03  9984  0.965505  0.970558  0.979058  0.992856  0.893760   
600498  2021-12-03  9987  1.018033  1.017600  1.004918  1.022544  0.658057   
600499  2021-12-03  9989  1.020275  1.015703  1.016844  1.023074  1.285089   

          target      macd    rsi_30    cci_30     dx_30  
0   

In [2]:
from easydict import EasyDict

trading0_ppo_config = dict(
    exp_name='trading_strategy_jpx_onppo_seed0',
    env=dict(
        collector_env_num=8,
        evaluator_env_num=1,
        n_evaluator_episode=1,
        stop_value=10000000000000000,
    ),
    policy=dict(
        cuda=False,
        action_space='continuous',
        model=dict(
            obs_shape=[4500],
            action_shape=500,
            action_space='continuous',
            encoder_hidden_size_list=[9000,128],
            critic_head_hidden_size=128,
            actor_head_hidden_size=128,
        ),
        learn=dict(
            epoch_per_collect=2,
            batch_size=64,
            learning_rate=0.001,
            value_weight=0.5,
            entropy_weight=0.01,
            clip_ratio=0.2,
            learner=dict(save_ckpt_after_iter=100
            ),
        ),
        collect=dict(
            n_sample=256,
            unroll_len=1,
            discount_factor=0.9,
            gae_lambda=0.95,
        ),
        eval=dict(evaluator=dict(eval_freq=100,),
        hook=dict()
        ),
    )
)
trading0_ppo_config = EasyDict(trading0_ppo_config)
main_config = trading0_ppo_config
trading0_ppo_create_config = dict(
    env=dict(
        type='cartpole',
        import_names=['dizoo.classic_control.cartpole.envs.cartpole_env'],
    ),
    env_manager=dict(type='base'),
    policy=dict(type='ppo'),
)
trading0_ppo_create_config = EasyDict(trading0_ppo_create_config)
create_config = trading0_ppo_create_config


In [3]:
# Process your data here [doing data  cleaning, features engineering here]
tech_indicator_list = ['open', 'high', 'low', 'close', 'volume', 'macd', 'rsi_30', 'cci_30', 'dx_30']

stock_dimension = len(train.tic.unique())
state_space = stock_dimension
print(f"Stock Dimension: {stock_dimension}, State Space: {state_space}")
feature_dimension = len(tech_indicator_list)
print(f"Feature Dimension: {feature_dimension}")

env_train_kwargs = {
    'df': train,
    "hmax": 100,
    "initial_amount": 0,
    "transaction_cost_pct": 0,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": tech_indicator_list,
    "action_space": stock_dimension,
    "reward_scaling": 1e-1
}

env_test_kwargs = {
    'df': test,
    "hmax": 100,
    "initial_amount": 0,
    "transaction_cost_pct": 0,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": tech_indicator_list,
    "action_space": stock_dimension,
    "reward_scaling": 1e-1
}

run_whole_train_kwargs = {
    'df': whole_data,
    "hmax": 100,
    "initial_amount": 0,
    "transaction_cost_pct": 0,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": tech_indicator_list,
    "action_space": stock_dimension,
    "reward_scaling": 1e-1,
    "run_whole_train": True,
}


Stock Dimension: 500, State Space: 500
Feature Dimension: 9


In [4]:
import gym
import sys, os
sys.path.insert(0, os.getcwd())

from model.vac import VAC
from ditk import logging
from ding.policy import PPOPolicy
from ding.envs import DingEnvWrapper, BaseEnvManagerV2
from ding.data import DequeBuffer
from ding.config import compile_config
from ding.framework import task
from ding.framework.context import OnlineRLContext
from ding.framework.middleware import multistep_trainer, StepCollector, interaction_evaluator, CkptSaver, gae_estimator, termination_checker
from ding.utils import set_pkg_seed




def render_whole_train():
    def _rwt(ctx):
        if ctx.total_step % 100 == 0:
            print(ctx.total_step)
            os.rename("/mnt/lustre/chenyun/jpx_trading/example/results/whole_cumulative_reward.png",
                "/mnt/lustre/chenyun/jpx_trading/example/results/whole_cumulative_reward_"+ str(ctx.total_step) + ".png")
    return _rwt

def trainer(env_name, main_config, create_config, env_train_kwargs, run_whole_train_kwargs, max_train_iter):
    logging.getLogger().setLevel(logging.INFO)
    cfg = compile_config(main_config, create_cfg=create_config, auto=True)
    
    with task.start(async_mode=False, ctx=OnlineRLContext()):
        collector_env = BaseEnvManagerV2(
            env_fn=[
                lambda: DingEnvWrapper(gym.make("{}".format(env_name), **env_train_kwargs))
                for _ in range(cfg.env.collector_env_num)
            ],
            cfg=cfg.env.manager
        )

        run_whole_env = BaseEnvManagerV2(
            env_fn=[
                lambda: DingEnvWrapper(gym.make("{}".format(env_name), **run_whole_train_kwargs)) for _ in range(1)
            ],
            cfg=cfg.env.manager
        )
        print(env_test_kwargs)

        cfg.seed = 5
        set_pkg_seed(cfg.seed, use_cuda=cfg.policy.cuda)
        print("="*40, "cfg.policy.model")
        print(cfg.policy.model)
        model = VAC(**cfg.policy.model)
        policy = PPOPolicy(cfg.policy, model=model)
        # task.use(interaction_evaluator(cfg, policy.eval_mode, evaluator_env))
        task.use(interaction_evaluator(cfg, policy.eval_mode, run_whole_env))
        task.use(StepCollector(cfg, policy.collect_mode, collector_env))
        task.use(gae_estimator(cfg, policy.collect_mode))
        task.use(multistep_trainer(cfg, policy.learn_mode))
        task.use(CkptSaver(cfg, policy, train_freq=10000))
        task.use(termination_checker(max_train_iter=max_train_iter))
        # task.use(render_whole_train())
        task.run()

def tester(env_name, main_config, create_config, env_train_kwargs, env_test_kwargs, run_whole_train_kwargs, max_train_iter):
    logging.getLogger().setLevel(logging.INFO)
    cfg = compile_config(main_config, create_cfg=create_config, auto=True)
    with task.start(async_mode=False, ctx=OnlineRLContext()):
        collector_env = BaseEnvManagerV2(
            env_fn=[
                lambda: DingEnvWrapper(gym.make("{}".format(env_name), **run_whole_train_kwargs))
                for _ in range(cfg.env.collector_env_num)
            ],
            cfg=cfg.env.manager
        )
        evaluator_env = BaseEnvManagerV2(
            env_fn=[
                lambda: DingEnvWrapper(gym.make("{}".format(env_name), **run_whole_train_kwargs))
                for _ in range(cfg.env.evaluator_env_num)
            ],
            cfg=cfg.env.manager
        )

        set_pkg_seed(cfg.seed, use_cuda=cfg.policy.cuda)
        print("="*40, "cfg.policy")
        print(cfg.policy)
        model = VAC(**cfg.policy.model)
        policy = PPOPolicy(cfg.policy, model=model)

        task.use(interaction_evaluator(cfg, policy.eval_mode, evaluator_env))
        task.run()


[11-18 13:39:54] WARNING  If you want to use numba to speed up segment tree, please install numba first                                              ]8;id=929070;file:///mnt/lustre/chenyun/DI-engine/ding/utils/default_helper.py\default_helper.py]8;;\:]8;id=428468;file:///mnt/lustre/chenyun/DI-engine/ding/utils/default_helper.py#410\410]8;;\

In [5]:
from gym.envs.registration import register
register(id='trading-v2', entry_point='env.portfolio_env:StockPortfolioEnvJpx', max_episode_steps=10000)
trainer('trading-v2', main_config, create_config, env_train_kwargs, run_whole_train_kwargs, 1e7)

[11-18 13:40:04] INFO     Env Space Information:                                                                                                   ]8;id=423818;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py\base_env_manager.py]8;;\:]8;id=9520;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py#128\128]8;;\

[11-18 13:40:04] INFO             Observation Space: Box([[[-inf -inf -inf ... -inf -inf -inf]                                                     ]8;id=19977;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py\base_env_manager.py]8;;\:]8;id=706840;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py#129\129]8;;\
                            [-inf -inf -inf ... -inf -inf -inf]                                                                                                           
                            [-inf -inf -inf ... -inf -inf -inf]                                                                                                           
                            ...                                                                                                                                           
                            [-inf -inf -inf ... -inf -inf -inf]                                                                                                           
                            [-inf -inf -inf ... -inf -inf -inf]                                                                                                           
                            [-inf -inf -inf ... -inf -inf -inf]]], [[                                                                                                     
                                                                                                                                                                          
                                                                                                                                                                          
                            ...                                                                                                                                           
                                                                                                                                                                          
                                                                                                                                                                          
                            ]], (1, 509, 500), float32)                                                                                                                   

[11-18 13:40:04] INFO             Action Space: Box([0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                       ]8;id=759810;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py\base_env_manager.py]8;;\:]8;id=297990;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py#130\130]8;;\
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.                                                                        
                           0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.], [1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.                        
                          1. 1. 1. 1. 1.                                                                                                                                  
                           1. 1.

[11-18 13:40:04] INFO             Reward Space: Box([-inf], , (1,), float32)                                                                       ]8;id=684915;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py\base_env_manager.py]8;;\:]8;id=146513;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py#131\131]8;;\

++++++++++++++++++++++++++++++++++++++++++++++++++ ['2017-01-04' '2017-01-05' '2017-01-06' ... '2021-12-01' '2021-12-02'
 '2021-12-03']
{'df':            date   tic      open      high       low     close    volume  \
0    2020-11-24  1407  1.044987  1.068010  1.041505  1.063131  3.017108   
0    2020-11-24  1414  1.031895  1.025688  1.030075  1.024074  1.434322   
0    2020-11-24  1435  1.011050  1.005435  1.016760  1.011050  1.108707   
0    2020-11-24  1515  1.033099  1.023438  1.018072  0.996071  0.985075   
0    2020-11-24  1766  1.038071  1.030864  1.036896  1.024691  1.204301   
..          ...   ...       ...       ...       ...       ...       ...   
251  2021-12-02  9936  1.000000  1.006803  1.001733  1.005155  1.463343   
251  2021-12-02  9983  0.982310  0.996771  0.985768  1.000894  1.060721   
251  2021-12-02  9984  0.960220  0.960000  0.953849  0.948983  1.266637   
251  2021-12-02  9987  0.993485  1.008065  0.995106  1.004854  1.509049   
251  2021-12-02  9989  0.984772 

...

/mnt/lustre/chenyun/jpx_trading/example/env/portfolio_env.py:230: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  purchase = (one_day_data.sort_values(by='rank')['target'][:portfolio_size] * weights).sum() / weights.mean()
/mnt/lustre/chenyun/jpx_trading/example/env/portfolio_env.py:231: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  short = (one_day_data.sort_values(by='rank', ascending=False)['target'][:portfolio_size] * weights).sum() / weights.mean()
/mnt/lustre/chenyun/jpx_trad

final_sharpe_ratio:-0.10640613947638342
Sharpe:  -0.10619480631945621
final_sharpe_ratio:-0.09211750446684966
Sharpe:  -0.09193454995761707
final_sharpe_ratio:0.04530722970215585
Sharpe:  0.04521724504589731
final_sharpe_ratio:0.05043675934172356
Sharpe:  0.05033658693034468
final_sharpe_ratio:0.037371765308647414
Sharpe:  0.03729754127250173
final_sharpe_ratio:-0.0006782958621323633
Sharpe:  -0.0006769486992094299
final_sharpe_ratio:-0.0075651255313806155
Sharpe:  -0.007550100441014921
final_sharpe_ratio:-0.029544138531967686
Sharpe:  -0.0294854609397218


/mnt/lustre/chenyun/jpx_trading/example/env/portfolio_env.py:230: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  purchase = (one_day_data.sort_values(by='rank')['target'][:portfolio_size] * weights).sum() / weights.mean()
/mnt/lustre/chenyun/jpx_trading/example/env/portfolio_env.py:231: FutureWarning: The behavior of `series[i:j]` with an integer-dtype index is deprecated. In a future version, this will be treated as *label-based* indexing, consistent with e.g. `series[i]` lookups. To retain the old behavior, use `series.iloc[i:j]`. To get the future behavior, use `series.loc[i:j]`.
  short = (one_day_data.sort_values(by='rank', ascending=False)['target'][:portfolio_size] * weights).sum() / weights.mean()
/mnt/lustre/chenyun/jpx_trad

[11-18 13:41:44] ERROR    Env 4 step has exceeded max retries(1)                                                                                   ]8;id=399253;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py\base_env_manager.py]8;;\:]8;id=570174;file:///mnt/lustre/chenyun/DI-engine/ding/envs/env_manager/base_env_manager.py#375\375]8;;\

RuntimeError: Env 4 step has exceeded max retries(1), and the latest exception is: 